In [1]:
import pandas as pd
import altair as alt

# Look at the metadata

In [2]:
metadata_df = pd.read_json('../../data/covidtracking/states-metadata.json')

In [3]:
metadata_df.head()

state                                     covid19SiteOld  \
0    AK  http://dhss.alaska.gov/dph/Epi/id/Pages/COVID-...   
1    AL  http://www.alabamapublichealth.gov/infectiousd...   
2    AR  https://www.healthy.arkansas.gov/programs-serv...   
3    AS  http://www.samoagovt.ws/2020/03/ministry-of-he...   
4    AZ  https://www.azdhs.gov/preparedness/epidemiolog...   

                                         covid19Site  \
0  http://dhss.alaska.gov/dph/Epi/id/Pages/COVID-...   
1  https://alpublichealth.maps.arcgis.com/apps/op...   
2  https://adem.maps.arcgis.com/apps/opsdashboard...   
3      http://www.samoagovt.ws/category/latest-news/   
4  https://www.azdhs.gov/preparedness/epidemiolog...   

                                covid19SiteSecondary          twitter  \
0  http://dhss.alaska.gov/dph/Epi/id/Pages/COVID-...     @Alaska_DHSS   
1                                               None  @alpublichealth   
2  https://www.healthy.arkansas.gov/programs-serv...          @adhpio   
3                 https://www.facebook.com/amsamgov/             None   
4                                               None           @azdhs   

        pui    pum                                              notes  \
0  All data  False  We count the reported number as "persons teste...   
1   No data  False  Last negative count from 3/16. Last update tim...   
2  All data   True  The state reports "specimens" tested, but it a...   
3   No Data  False   American Samoa: No data, no confirmed cases yet.   
4  All data  False  Negative = “Ruled Out”. Negatives are from pub...   

             name  
0          Alaska  
1         Alabama  
2        Arkansas  
3  American Samoa  
4         Arizona

# Look at the data

In [4]:
data_df = pd.read_json('../../data/covidtracking/states-daily.json')
data_df['date'] = pd.to_datetime(data_df['date'], format="%Y%m%d")

In [5]:
data_df.head()

date state  positive  negative  pending  hospitalized  death  total  \
0 2020-03-23    AK      22.0     946.0      NaN           0.0    NaN    968   
1 2020-03-23    AL     167.0    1665.0      NaN           NaN    0.0   1832   
2 2020-03-23    AR     174.0     906.0      0.0          13.0    0.0   1080   
3 2020-03-23    AS       NaN       NaN      NaN           NaN    0.0      0   
4 2020-03-23    AZ     265.0     309.0      6.0           NaN    2.0    580   

            dateChecked  
0  2020-03-23T20:00:00Z  
1  2020-03-23T20:00:00Z  
2  2020-03-23T20:00:00Z  
3  2020-03-23T20:00:00Z  
4  2020-03-23T20:00:00Z

### Daily counts and totals

In [6]:
# compute daily differences
tdf = data_df.sort_values(['state', 'date'], ascending=[True, False]).set_index(['state', 'date'])
diffs_df = tdf[['positive', 'negative', 'death']].groupby(level='state').diff(periods=-1).dropna(how='all')
tdf_diff=tdf.join(diffs_df, rsuffix='_diff').reset_index()

# "Normalizing" the totals
tdf_diff['total_10'] = tdf_diff['total']/10.

In [7]:
tdf

positive  negative  pending  hospitalized  death  total  \
state date                                                                  
AK    2020-03-23      22.0     946.0      NaN           0.0    NaN    968   
      2020-03-22      22.0     946.0      NaN           0.0    NaN    968   
      2020-03-21      14.0     758.0      NaN           0.0    NaN    772   
      2020-03-20      12.0     686.0      NaN           NaN    NaN    698   
      2020-03-19       6.0     400.0      NaN           NaN    NaN    406   
...                    ...       ...      ...           ...    ...    ...   
WY    2020-03-11       0.0       NaN      NaN           NaN    NaN      0   
      2020-03-10       0.0       0.0      0.0           NaN    NaN      0   
      2020-03-09       0.0       NaN      NaN           NaN    NaN      0   
      2020-03-08       0.0       NaN      NaN           NaN    NaN      0   
      2020-03-07       0.0       NaN      NaN           NaN    NaN      0   

                           dateChecked  
state date                              
AK    2020-03-23  2020-03-23T20:00:00Z  
      2020-03-22  2020-03-22T20:00:00Z  
      2020-03-21  2020-03-21T20:00:00Z  
      2020-03-20  2020-03-20T20:00:00Z  
      2020-03-19  2020-03-19T20:00:00Z  
...                                ...  
WY    2020-03-11  2020-03-11T20:00:00Z  
      2020-03-10  2020-03-10T20:00:00Z  
      2020-03-09  2020-03-09T20:00:00Z  
      2020-03-08  2020-03-08T20:00:00Z  
      2020-03-07  2020-03-07T21:00:00Z  

[981 rows x 7 columns]

In [8]:
tdf_diff

state       date  positive  negative  pending  hospitalized  death  total  \
0      AK 2020-03-23      22.0     946.0      NaN           0.0    NaN    968   
1      AK 2020-03-22      22.0     946.0      NaN           0.0    NaN    968   
2      AK 2020-03-21      14.0     758.0      NaN           0.0    NaN    772   
3      AK 2020-03-20      12.0     686.0      NaN           NaN    NaN    698   
4      AK 2020-03-19       6.0     400.0      NaN           NaN    NaN    406   
..    ...        ...       ...       ...      ...           ...    ...    ...   
976    WY 2020-03-11       0.0       NaN      NaN           NaN    NaN      0   
977    WY 2020-03-10       0.0       0.0      0.0           NaN    NaN      0   
978    WY 2020-03-09       0.0       NaN      NaN           NaN    NaN      0   
979    WY 2020-03-08       0.0       NaN      NaN           NaN    NaN      0   
980    WY 2020-03-07       0.0       NaN      NaN           NaN    NaN      0   

              dateChecked  positive_diff  negative_diff  death_diff  total_10  
0    2020-03-23T20:00:00Z            0.0            0.0         NaN      96.8  
1    2020-03-22T20:00:00Z            8.0          188.0         NaN      96.8  
2    2020-03-21T20:00:00Z            2.0           72.0         NaN      77.2  
3    2020-03-20T20:00:00Z            6.0          286.0         NaN      69.8  
4    2020-03-19T20:00:00Z            0.0           -6.0         NaN      40.6  
..                    ...            ...            ...         ...       ...  
976  2020-03-11T20:00:00Z            0.0            NaN         NaN       0.0  
977  2020-03-10T20:00:00Z            0.0            NaN         NaN       0.0  
978  2020-03-09T20:00:00Z            0.0            NaN         NaN       0.0  
979  2020-03-08T20:00:00Z            0.0            NaN         NaN       0.0  
980  2020-03-07T21:00:00Z            NaN            NaN         NaN       0.0  

[981 rows x 13 columns]

In [9]:
# produce the charts for a few states

charts=[]
for state in ['WA', 'CA', 'NY']: 
    state_df = tdf_diff[tdf_diff['state'] == state].copy()

    state_df.loc[:,'daily_positive'] = state_df['positive'][::-1].diff()
    state_df.loc[:,'total_10'] = state_df['total']/10.

    base = alt.Chart(state_df, title=state).encode(alt.X('date', axis=alt.Axis(title='Date'))).properties(width=250, height=150)
    dailies = base.mark_bar(size=10).encode(alt.Y('daily_positive', axis=alt.Axis(title='Daily positive')))

    totals = base.mark_line(color='red').encode(alt.Y('total_10', axis=alt.Axis(title='Total/10'))) 
    positives = totals.mark_line(color='orange').encode(alt.Y('positive', axis=alt.Axis(title='Positive')))
    cumulative = totals + positives

    charts.append(alt.layer(dailies, cumulative).resolve_scale(y='independent'))


alt.hconcat(*charts)

alt.HConcatChart(...)

### Counts per 100k

In [10]:
pop_df = pd.read_csv('../../data/geodata/us_pop_fung_2019.csv').set_index('ST')

In [11]:
most_recent_test_date = data_df['date'].max()
most_recent_df = data_df[data_df['date'] == most_recent_test_date].set_index('state')
print("Most recent test date", most_recent_test_date)
print(len(most_recent_df), "states/territories have data on this date.")

Most recent test date 2020-03-23 00:00:00
56 states/territories have data on this date.


In [12]:
most_recent_df['total/100k'] = (most_recent_df['total'] / pop_df['Population']) * 100000
most_recent_df = most_recent_df.reset_index()

In [13]:
most_recent_df.head()

state       date  positive  negative  pending  hospitalized  death  total  \
0    AK 2020-03-23      22.0     946.0      NaN           0.0    NaN    968   
1    AL 2020-03-23     167.0    1665.0      NaN           NaN    0.0   1832   
2    AR 2020-03-23     174.0     906.0      0.0          13.0    0.0   1080   
3    AS 2020-03-23       NaN       NaN      NaN           NaN    0.0      0   
4    AZ 2020-03-23     265.0     309.0      6.0           NaN    2.0    580   

            dateChecked  total/100k  
0  2020-03-23T20:00:00Z  132.322687  
1  2020-03-23T20:00:00Z   37.363469  
2  2020-03-23T20:00:00Z   35.787363  
3  2020-03-23T20:00:00Z         NaN  
4  2020-03-23T20:00:00Z    7.968437

In [14]:
chart = alt.Chart(most_recent_df.sort_values('total/100k'), title="Tests per 100k")
chart.mark_bar().encode(alt.X('state', sort='y'), alt.Y('total/100k'))

alt.Chart(...)